In [1]:
import transformers
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

tokenizer = AutoTokenizer.from_pretrained("lmsys/fastchat-t5-3b-v1.0")

model = AutoModelForSeq2SeqLM.from_pretrained("lmsys/fastchat-t5-3b-v1.0")

You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. If you see this, DO NOT PANIC! This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=True`. This should only be set if you understand what it means, and thouroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565
C:\Users\SudheerRChinthala\anaconda3\Lib\site-packages\transformers\utils\generic.py:260: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  torch.utils._pytree._register_pytree_node(
C:\Users\SudheerRChinthala\anaconda3\Lib\site-packages\transformers\utils\generic.py:260: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  torch.utils._pytre

In [2]:
from transformers import pipeline
from langchain.llms import HuggingFacePipeline
import torch

pipe = pipeline(
    "text2text-generation",
    model=model, 
    tokenizer=tokenizer, 
    max_length=256
)

local_llm = HuggingFacePipeline(pipeline=pipe)

In [3]:
print(local_llm('What is the capital of Telangana?'))

C:\Users\SudheerRChinthala\anaconda3\Lib\site-packages\langchain_core\_api\deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


<pad> hyderabad


In [4]:
import os

In [5]:
from langchain.vectorstores import Chroma
from langchain.text_splitter import RecursiveCharacterTextSplitter

from langchain.chains import RetrievalQA
from langchain.document_loaders import TextLoader
from langchain.document_loaders import PyPDFLoader
from langchain.document_loaders import DirectoryLoader


from InstructorEmbedding import INSTRUCTOR
from langchain.embeddings import HuggingFaceInstructEmbeddings

In [17]:
#!pip install SQLAlchemy==1.4.46

  Using cached SQLAlchemy-1.4.46-cp311-cp311-win_amd64.whl (1.6 MB)
  Attempting uninstall: SQLAlchemy
    Found existing installation: SQLAlchemy 2.0.25
    Uninstalling SQLAlchemy-2.0.25:
      Successfully uninstalled SQLAlchemy-2.0.25


ERROR: Could not install packages due to an OSError: [WinError 5] Access is denied: 'C:\\Users\\SudheerRChinthala\\anaconda3\\Lib\\site-packages\\~-lalchemy\\cyextension\\collections.cp311-win_amd64.pyd'
Consider using the `--user` option or check the permissions.



In [6]:
# Load and process the text files
# loader = TextLoader('single_text_file.txt')
loader = DirectoryLoader('C:/Users/SudheerRChinthala/sivallm/new_papers', glob="./*.pdf", loader_cls=PyPDFLoader)

#documents = loader.load()

In [7]:
documents = loader.load()

In [8]:
len(documents)

25

In [9]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
texts = text_splitter.split_documents(documents)

In [10]:
len(texts)

43

In [11]:
texts[3]

Document(page_content='Release N otes for ICORE and INSTAR Release Dec 2023 Feature                                            \n3 \n Purpose \n \nThe purpose of this document is to provide release notes for the ICORE and INSTAR portion of the Nov \nand Dec 2023 release.  \n   \nDocument History \nVersion  Issue Date  Author(s)  Identification of Changes  \n      .01', metadata={'source': 'C:\\Users\\SudheerRChinthala\\sivallm\\new_papers\\ICORE_INSTAR_Dec_2003_Release_Notes.pdf', 'page': 2})

In [12]:
from langchain.embeddings import HuggingFaceInstructEmbeddings

In [13]:
from langchain_community.embeddings import HuggingFaceInstructEmbeddings

In [5]:
!pip install InstructorEmbedding

In [14]:
#from InstructorEmbedding import INSTRUCTOR
from langchain.embeddings import HuggingFaceInstructEmbeddings

In [16]:
from langchain_community.vectorstores import Chroma

In [17]:
instructor_embeddings = HuggingFaceInstructEmbeddings(model_name="hkunlp/instructor-base") 
                                                      

load INSTRUCTOR_Transformer
max_seq_length  512


In [18]:
persist_directory = 'db'
## Here is the nmew embeddings being used
embedding = instructor_embeddings

In [19]:
vectordb = Chroma.from_documents(documents=texts, 
                                 embedding=embedding,
                                 persist_directory=persist_directory)

In [20]:
retriever = vectordb.as_retriever(search_kwargs={"k": 3})

In [69]:
import textwrap

def wrap_text_preserve_newlines(text, width=110):
    # Split the input text into lines based on newline characters
    lines = text.split('\n')

    # Wrap each line individually
    wrapped_lines = [textwrap.fill(line, width=width) for line in lines]

    # Join the wrapped lines back together using newline characters
    wrapped_text = '\n'.join(wrapped_lines)

    return wrapped_text

def process_llm_response(llm_response):
    print(wrap_text_preserve_newlines(llm_response['result']))
    print('\n\nSources:')
    for source in llm_response["source_documents"]:
        print(source.metadata['source'])

In [71]:
qa_chain = RetrievalQA.from_chain_type(llm=local_llm, 
                                  chain_type="stuff", 
                                  retriever=retriever, 
                                  return_source_documents=True)

In [72]:
query = "Are Service Options ordered from USRP"
llm_response = qa_chain(query)
print(llm_response)
process_llm_response(llm_response)

C:\Users\SudheerRChinthala\anaconda3\Lib\site-packages\langchain_core\_api\deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.0 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


<pad> No,  Service  Options  are  not  ordered  from  USRP.



Sources:
C:\Users\SudheerRChinthala\sivallm\new_papers\ICORE_INSTAR_Release_Notes.pdf
C:\Users\SudheerRChinthala\sivallm\new_papers\ICORE_INSTAR_Release_Notes.pdf
C:\Users\SudheerRChinthala\sivallm\new_papers\ICORE_INSTAR_Release_Notes.pdf


In [73]:
vectordb.persist()
vectordb = None

In [74]:
vectordb = Chroma(persist_directory=persist_directory, 
                  embedding_function=embedding)

In [75]:
retriever = vectordb.as_retriever()

In [76]:
qa_chain = RetrievalQA.from_chain_type(llm=local_llm, 
                                  chain_type="stuff", 
                                  retriever=retriever, 
                                  return_source_documents=True)

In [21]:
query = "Can you give me information about Shared, Port tagging No"
llm_response = qa_chain(query)
process_llm_response(llm_response)

NameError: name 'qa_chain' is not defined